<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Read-DataFrame" data-toc-modified-id="Read-DataFrame-1">Read DataFrame</a></span></li><li><span><a href="#Folium" data-toc-modified-id="Folium-2">Folium</a></span><ul class="toc-item"><li><span><a href="#Using-Markers" data-toc-modified-id="Using-Markers-2.1">Using Markers</a></span></li><li><span><a href="#Using-Choropleth-Maps" data-toc-modified-id="Using-Choropleth-Maps-2.2">Using Choropleth Maps</a></span></li><li><span><a href="#Heatmaps" data-toc-modified-id="Heatmaps-2.3">Heatmaps</a></span></li></ul></li><li><span><a href="#Plotly" data-toc-modified-id="Plotly-3">Plotly</a></span><ul class="toc-item"><li><span><a href="#Scatter-Geo" data-toc-modified-id="Scatter-Geo-3.1">Scatter Geo</a></span></li><li><span><a href="#Density-Heatmap" data-toc-modified-id="Density-Heatmap-3.2">Density Heatmap</a></span></li><li><span><a href="#Animation" data-toc-modified-id="Animation-3.3">Animation</a></span></li></ul></li></ul></div>

## Read DataFrame

In [22]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

In [23]:
df = pd.read_csv('time_series_covid_19_confirmed.csv')

df['Country/Region'].replace({'Mainland China':'China',
                              'US':'United States of America',
                              'UK':'United Kingdom'},
                             inplace=True)

In [24]:
df.head()

Country/Region Province/State       Lat      Long  1/22/2020  1/23/2020  \
0          China          Anhui  31.82571  117.2264        1.0        9.0   
1          China        Beijing  40.18238  116.4142       14.0       22.0   
2          China      Chongqing  30.05718  107.8740        6.0        9.0   
3          China         Fujian  26.07783  117.9895        1.0        5.0   
4          China          Gansu  36.06110  103.8343        0.0        2.0   

   1/24/2020  1/25/2020  1/26/2020  1/27/2020    ...     2/12/2020  2/13/2020  \
0       15.0       39.0       60.0       70.0    ...         889.0      910.0   
1       36.0       41.0       68.0       80.0    ...         352.0      366.0   
2       27.0       57.0       75.0      110.0    ...         518.0      529.0   
3       10.0       18.0       35.0       59.0    ...         272.0      279.0   
4        2.0        4.0        7.0       14.0    ...          87.0       90.0   

   2/14/2020  2/15/2020  2/16/2020  2/17/2020  2/18/2020  2/19/2020  \
0      934.0      950.0      962.0      973.0      982.0      986.0   
1      372.0      375.0      380.0      381.0      387.0      393.0   
2      537.0      544.0      551.0      553.0      555.0      560.0   
3      281.0      285.0      287.0      290.0      292.0      293.0   
4       90.0       90.0       90.0       91.0       91.0       91.0   

   2/20/2020  3/1/2020  
0      987.0       987  
1      395.0       395  
2      567.0       567  
3      293.0       293  
4       91.0        91  

[5 rows x 35 columns]

In [25]:
df1 = pd.melt(df, id_vars=['Country/Region', 'Province/State','Lat','Long'])
df1.head()

Country/Region Province/State       Lat      Long   variable  value
0          China          Anhui  31.82571  117.2264  1/22/2020    1.0
1          China        Beijing  40.18238  116.4142  1/22/2020   14.0
2          China      Chongqing  30.05718  107.8740  1/22/2020    6.0
3          China         Fujian  26.07783  117.9895  1/22/2020    1.0
4          China          Gansu  36.06110  103.8343  1/22/2020    0.0

In [84]:
df1 = df1.rename(columns={'variable':'date','value':'cases'})

## Folium

In [26]:
import folium
from folium import plugins

### Using Markers

In [27]:
# Create Map Object m
m1 = folium.Map(location=[37,-9],zoom_start=2,
               tiles = "CartoDB positron")

In [28]:
for index, row in df.iterrows():    
    _radius = int(row['3/1/2020']) 
    
    if np.isnan(_radius):
        _radius = 0
  
    lat, lon = row['Lat'], row['Long']  
    folium.CircleMarker(location = [lat,lon], 
                        radius = _radius/10000, 
                        color = '#E80018',
                        fill=True,
                        fill_opacity = 1).add_to(m1)

In [29]:
display(m1)

In [30]:
m1.save('folium-dots.html')

### Using Choropleth Maps

the worlds' countries coordinates are uploaded using the json fil `custom.geo.json` where the match to the dataframe will be using `columns` where the first argument is column name and the second is the data to capture from the df. `key_on` specifies which feature on the JSON file contains the data to match with the `Country/Region` chosen in `columns` attribute.

In [31]:
list(df['3/1/2020'].quantile([0.3, 0.5, 0.6, 0.7, 0.8, 0.9, 0.95, 0.98, 1]))

[5.5, 16.5, 46.0, 119.0, 293.0, 784.0, 1139.75, 1572.3999999999862, 62442.0]

In [32]:
m2 = folium.Map(location=[37,-9],zoom_start=2,
               tiles = "CartoDB positron")

In [33]:
# Specifying my Bins
bins = list(df['3/1/2020'].quantile([0, 0.3, 0.4, 0.5, 0.9, 0.95, 1]))

# Using Choropleth Maps
folium.Choropleth(geo_data="custom.geo.json",
             data=df, # my dataset
             columns=['Country/Region', '3/1/2020'], # country/region is here for matching the geojson country names, '20-02-2020' is the column that changes the color of zipcode areas
             key_on='feature.properties.sovereignt', # this path contains name of country to match with data, this should match with our 'Country/Region' column
             fill_color='PuRd', 
             fill_opacity=1,
             line_opacity=1,
             legend_name='# of Cases',
             bins=bins,
            reset=True).add_to(m2)

display(m2)

In [34]:
m2.save('folium-choropleth.html')

### Heatmaps

In [35]:
m3 = folium.Map(location=[37,-9],zoom_start=2)

In [36]:
from folium.plugins import HeatMap

heat_data = [[row['Lat'],row['Long']] for index, row in df.iterrows()]

# Plot it on the map
HeatMap(heat_data).add_to(m3)

In [37]:
m3

In [38]:
m3.save('folium-heat.html')

---------------------------

## Plotly

In [39]:
import plotly.express as px

In [40]:
df1.head()

Country/Region Province/State       Lat      Long   variable  value
0          China          Anhui  31.82571  117.2264  1/22/2020    1.0
1          China        Beijing  40.18238  116.4142  1/22/2020   14.0
2          China      Chongqing  30.05718  107.8740  1/22/2020    6.0
3          China         Fujian  26.07783  117.9895  1/22/2020    1.0
4          China          Gansu  36.06110  103.8343  1/22/2020    0.0

### Scatter Geo

In [85]:
data = df1[df1.date=='3/1/2020']

In [86]:
fig1 = px.scatter_geo(data,
                     lat= 'Lat',
                     lon= 'Long',
                     hover_name="Country/Region",
                     projection="natural earth",
                     title='Scatter Geo of Coronavirus on 1st March 2020')
fig1.show()

In [59]:
fig1.write_image("scatter_geo.png")

### Density Heatmap

In [102]:
fig2 = px.density_mapbox(data,
                     lat = 'Lat',
                     lon= 'Long',
                     radius=10,
                     center=dict(lat=37, lon=-9),
                     zoom=1,
                     hover_name="Country/Region",
                     mapbox_style="carto-darkmatter",
                     title='World Heatmap of Coronavirus on 1st March 2020')
fig2.show()

In [61]:
fig2.write_image("plotly-heatmap.png")

### Animation

In [98]:
df1 = df1[df1.cases.notnull()]

In [100]:
fig2 = px.scatter_geo(df1,
                     lat= 'Lat',
                     lon= 'Long',
                     center=dict(lat=37, lon=-9),
                     hover_name="Country/Region",
                     animation_frame='date')
fig2.show()